In [1]:
from insolAPI.WebAPI import API
import simplejson as json
import pandas as pd
import pendulum as pdl
import matplotlib.pyplot as plt
import plotly.graph_objects as go
from datetime import datetime, timedelta
import warnings
from tqdm import tqdm
import sys
from tabulate import tabulate
from pytz import timezone

In [34]:
time_args = dict(
    start=pdl.yesterday().subtract(weeks=1).to_datetime_string(),
    stop=(pdl.now()).to_datetime_string(),
    timezone = timezone('Europe/Zurich')
)

def read_json_config():
    """
    Read the config.json file and return the api key
    """
    with open("config.json") as f:
        config_data = json.load(f)

    installations = {}

    # Iterate through locations
    locations = config_data['locations']
    for location in locations:
        # Store details in a dictionary
        location_details = {
            'id': location['id'],
            'name': location['name'],
            'latitude': location['latitude'],
            'longitude': location['longitude'],
            'wind_threshold': location['wind_threshold'],
            'high_temperature_threshold': location['high_temperature_threshold'],
            'has_a_screen': location['has_a_screen'],
        }
        installations[location['name']] = location_details
    return installations, [config_data['api_key'], config_data['api_url']]


installation_path = "C:/Users/Insolight/Desktop/InsolReports/Scripts"
with open(installation_path + "/local.json") as f:
    local_data = json.load(f)
api = API(local_data["API_user"], local_data["API_pwd"], dev_space=False)

list_sensor = [
    "PAR",
    "IRRAD",
    "GII",
    "DNI",
    "DHI",
    "TEMP",
    "HUMI",
    "RAIN",
    "RAIN_TYPE",
    "RAIN_ACCUMULATED",
    "WIND",
    "WIND_DIR",
    "VIRTUAL",
    "LEAF_TEMP"
]

dict_instal = {
    "Etchelecu": 26,
    "Agroscope Series": 24,
    "Agroscope Berries": 25,
    "Bioschmid": 23,
}

In [35]:
logs_joined = {}
for instal in tqdm(dict_instal):
    logs_joined[instal] = {}
    sensor_number = 0
    for sensor_type in api.SensorsTypes:
        if str(sensor_type).split(".")[1] in list_sensor:
            with warnings.catch_warnings():
                warnings.simplefilter("ignore", category=UserWarning)
                logs_joined[instal][list_sensor[sensor_number]] = api.get_sensor_channels_logs_joined(**time_args,sensor_type=sensor_type, install=dict_instal[instal])
                sensor_number += 1

100%|██████████| 4/4 [00:43<00:00, 10.88s/it]


In [62]:
unique_sensors = {}
logs_joined_unique = {}
last_log = {}
for instal in dict_instal:
    print(instal)
    unique_sensors[instal] = []
    for sensor_type in logs_joined[instal]:
        try:
            unique_sensors[instal].extend(logs_joined[instal][sensor_type]["sensor_name"].unique())
        except :
            pass
    unique_sensors[instal] = list(set(unique_sensors[instal]))
    logs_joined_unique[instal] = {}
    for sensor_type in logs_joined[instal]:
        for unique_sensor in unique_sensors[instal]:
            try:
                if unique_sensor in logs_joined[instal][sensor_type]["sensor_name"].unique():
                    logs_joined_unique[instal][unique_sensor] = logs_joined[instal][sensor_type].loc[logs_joined[instal][sensor_type]["sensor_name"] == unique_sensor]
                    logs_joined_unique[instal][unique_sensor].index = logs_joined_unique[instal][unique_sensor].index.round('min')
                    logs_joined_unique[instal][unique_sensor] = logs_joined_unique[instal][unique_sensor].loc[~logs_joined_unique[instal][unique_sensor].index.duplicated(keep='first')]
            except :
                pass

    for sensor in logs_joined_unique[instal]:
        logs_joined_unique[instal][sensor] = logs_joined_unique[instal][sensor].dropna(subset=[logs_joined_unique[instal][sensor].columns[1]])

    last_log[instal] = {}
    for sensor in logs_joined_unique[instal]:
        last_log[instal][sensor] = logs_joined_unique[instal][sensor].index[-1]
        if last_log[instal][sensor] > pdl.now().subtract(minutes=10):
            last_log[instal][sensor] = "up to date"

Etchelecu
Agroscope Series
Agroscope Berries
Bioschmid


In [39]:
for i in last_log:
    print(i)
    print(tabulate(last_log[i].items(), headers=["Sensor", "Last log"], tablefmt="github"))
    print("\n")

Etchelecu
| Sensor                | Last log   |
|-----------------------|------------|
| PAR01_Insolagrin      | up to date |
| PAR02_Insolagrin      | up to date |
| PAR03_Insolagrin      | up to date |
| PAR04_Insolagrin      | up to date |
| PAR01_EXT             | up to date |
| PAR02_EXT             | up to date |
| PAR01_control         | up to date |
| PAR02_control         | up to date |
| GHI_01_EXT            | up to date |
| TRH_top_Insolagrin    | up to date |
| TRH_bottom_Insolagrin | up to date |
| TRH_top_EXT           | up to date |
| TRH_bottom_EXT        | up to date |
| TRH_top_control       | up to date |
| TRH_bottom_control    | up to date |
| RAIN_EXT              | up to date |
| WIND01_EXT            | up to date |
| WIND02_EXT            | up to date |


Agroscope Series
| Sensor                            | Last log   |
|-----------------------------------|------------|
| PAR1                              | up to date |
| PAR2                              | 

In [49]:
time_diff = {}
time_diff_mean = {}
for instal in logs_joined_unique:
    time_diff[instal] = {}
    time_diff_mean[instal] = {}
    for sensor in logs_joined_unique[instal]:
        time_diff_mean[instal][sensor] = logs_joined_unique[instal][sensor].index.to_series().diff()[1:].mean().total_seconds()
        time_diff_mean[instal][sensor] = logs_joined_unique[instal][sensor].index.to_series().diff()[1:]

KeyboardInterrupt: 

# Plot the distribution of the time between logs

In [51]:
time_diff = {}
for instal in dict_instal:
    time_diff[instal] = {}
    for unique_sensor in logs_joined_unique[instal]:
        #compute the time difference between two logs in seconds
        time_diff[instal][unique_sensor] = logs_joined_unique[instal][unique_sensor].index.to_series().diff()[1:]

In [ ]:
for instal in dict_instal:
    total_num_sensors = len(unique_sensors[instal])
    num_rows = total_num_sensors // 6
    fig = plt.figure()
    fig.set_figheight(7*num_rows)
    fig.set_figwidth(20)
    fig.suptitle(instal)
    for unique_sensor in unique_sensors[instal]:
        ax = fig.add_subplot(num_rows + 1, 6, unique_sensors[instal].index(unique_sensor) + 1)
        ax.hist(time_diff[instal][unique_sensor].dropna().dt.total_seconds(), bins=10, range=(61, 10000))
        ax.set_title(unique_sensor)
        ax.set_xlim(61, 10000)
        ax.grid(True)
        ax.set_yscale('log')
    fig.tight_layout()

In [ ]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

for instal in dict_instal:
    total_num_sensors = len(unique_sensors[instal])
    num_rows = total_num_sensors // 6

    fig = make_subplots(rows=num_rows + 1, cols=6, subplot_titles=unique_sensors[instal], shared_yaxes=True)
    fig.update_layout(title_text=instal)
    #set the height of the figure
    fig.update_layout(height=300*num_rows)

    for i, unique_sensor in enumerate(unique_sensors[instal]):
        row_num = i // 6 + 1
        col_num = i % 6 + 1

        trace = go.Histogram(
            x=time_diff[instal][unique_sensor].dropna().dt.total_seconds(),
            nbinsx=10,
            xbins=dict(start=61, end=10000),
            name=unique_sensor,
        )

        fig.add_trace(trace, row=row_num, col=col_num)

        fig.update_xaxes(row=row_num, col=col_num)
        fig.update_yaxes(row=row_num, col=col_num, type="log")

    fig.update_layout(showlegend=False)
    # fig.update_layout(subplot_titles_text={'size': 10})
    fig.show()
    #save the figure as a html file
    fig.write_html("hist log frequency/" + instal + "_time_diff.html")
